In [1]:
%matplotlib inline



# Outlier Analysis: 

### Here we use the percentile analysis for knowing how well this work



In [2]:
from pymongo import MongoClient
from __future__ import print_function
from sklearn.externals import joblib
from sklearn.cluster import KMeans
from sklearn import metrics 

import sys
sys.path.append('../../lib')
import rs_common_framework_v4 as rs

import pandas as pd
import datetime
import collections
import numpy as np
import math

from sklearn.decomposition import PCA, IncrementalPCA
from matplotlib import cm, pyplot as plt, style as st, gridspec as gd
from matplotlib.dates import YearLocator, MonthLocator
st.use('seaborn-colorblind')

import plotly.offline as py
import plotly.graph_objs as go  #important library for the plotly
#import cufflinks as cf
import pylab as pl
from IPython.display import display

py.init_notebook_mode(connected=False) # run at the start of every ipython notebook to use plotly.offline
from plotly import tools #to do subplots

from hmmlearn.hmm import GaussianHMM
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)
warnings.filterwarnings("ignore", category=RuntimeWarning)

print(__doc__)

Automatically created module for IPython interactive environment


In [3]:
print("\t Connected to Mongo DB")

season = ['winter', 'summer', 't_period_1', 't_period_2']
connection = MongoClient('localhost') #"192.168.6.132"
collection_series = 'filtered_time_series'
#collection_series = 'original_time_series'
collection_metadata = 'metadata'
collection_comfort_room_sax = 'comfort_room_sax'

MONGODB_HOST = 'localhost'  # '192.168.6.132'
MONGODB_PORT = 27017
MONGODB_DB = 'project_db'
connection = MongoClient(MONGODB_HOST, MONGODB_PORT)
collection_series = connection[MONGODB_DB][collection_series]
collection_metadata = connection[MONGODB_DB][collection_metadata]
collection_comfort_room_sax = connection[MONGODB_DB][collection_comfort_room_sax]

projection = {'timestamp': True}
time_query = {}  # all the timeline
tag_query = {}  # all variables
period = '1D'  # '1M'

	 Connected to Mongo DB


In [8]:
tag_query = {'category': 'Temperature', 'floor': {"$in": [1, 2, 3]}}
tag_query = {'category': 'Temperature', 'location': 'out'}
tag_query = {'category': 'Temperature', 'orientation': 'S'}
tag_list = rs.get_tag_names(collection_metadata, tag_query)

low_quartile = np.linspace(0.01, 0.25, 15)  # lower quartile
up_quartile = np.linspace(0.75, 0.99, 15)   # upper quartile
high_limit = 1.0  # This defines the high limit using the linear regression when x=1.0
low_limit = -0.0  # This defines the low limit using the linear regression when x=0.0

print('\tGet tag names to work with. \n\tDefining the lower and higher quartile: \n\n{0}, \n{1}'.format(low_quartile, up_quartile))

	Get tag names to work with. 
	Defining the lower and higher quartile: 

[ 0.01        0.02714286  0.04428571  0.06142857  0.07857143  0.09571429
  0.11285714  0.13        0.14714286  0.16428571  0.18142857  0.19857143
  0.21571429  0.23285714  0.25      ], 
[ 0.75        0.76714286  0.78428571  0.80142857  0.81857143  0.83571429
  0.85285714  0.87        0.88714286  0.90428571  0.92142857  0.93857143
  0.95571429  0.97285714  0.99      ]


In [9]:
def f_up_limit(values):
    df = pd.DataFrame(values)
    return rs.get_limit_by_quartile(df[0], up_quartile, high_limit)

def f_low_limit(values):
    df = pd.DataFrame(values)
    return rs.get_limit_by_quartile(df[0], low_quartile, low_limit)

In [10]:
detections = {}
df_ucl = pd.DataFrame() 
df_lcl = pd.DataFrame()
df_t = rs.get_tag_values(collection_series, time_query, tag_list, series_format='DF_idx')

for tag in tag_list:
    ''' Process data for each Tag
    '''
    detections[tag] = 0
    df = pd.DataFrame()
    df[tag] = df_t[tag].copy()
    df[tag] = pd.to_numeric(df[tag], errors='coerce')
    df[tag] = df[tag].fillna(df[tag].interpolate())

    #df_ucl[tag] = df[tag].rolling(window=10, min_periods=10, center=True).apply(f_up_limit)
    #df_lcl[tag] = df[tag].rolling(window=10, min_periods=10, center=True).apply(f_low_limit)

In [11]:
print(tag_list)
for tag in tag_list:
    trace0 = go.Scatter(
        x=df_t.index,
        y=df_t[tag],
        text=df_t.index.weekday_name,
        mode='lines',
        name = rs.get_alias(collection_metadata,tag),
        line=dict(
            color='green',
        )
    )
    #trace1 = go.Scatter(
    #    x=df_ucl.index,
    #    y=df_ucl[tag],
    #    mode='lines',
    #    name = 'Upper limit',
    #    line=dict(
    #        color='red',
    #        shape='hv'
    #    )
    #)
    #trace2 = go.Scatter(
    #    x=df_lcl.index,
    #    y=df_lcl[tag],
    #    mode='lines',
    #    name = 'Lower limit',
    #    line=dict(
    #        color='blue',
    #        shape='hv'
    #    )
    #)
    layout = go.Layout(
        title='Percentile analysis',
        xaxis=dict(
            title='Hours',
            dtick= 1,
            titlefont=dict(
                family='Courier New, monospace',
                size=18,
                color='#7f7f7f'
            )
        ),
        yaxis=dict(
            title=rs.get_alias(collection_metadata,tag),
            #range=[400,850],
            titlefont=dict(
                family='Courier New, monospace',
                size=18,
                color='#7f7f7f'
            )
        )
    ) 
    
    #data = [trace2, trace0, trace1]
    data = [trace0]
    fig = go.Figure(data=data)
    py.iplot(fig)

['V077_room103_temp', 'V081_room203_temp', 'V085_room303_temp']
